In [1]:
import os
import numpy as np
import pandas as pd
import re
import bagpy
import rosbag
import rospy
from std_msgs.msg import Float64
from geometry_msgs.msg import PointStamped
from sensor_msgs.msg import NavSatFix

from bagpy import bagreader

from pathlib import Path

from rosbags.highlevel import AnyReader
from rosbags.dataframe import get_dataframe


In [2]:
# The path from where you want to get the bag files
folder_path = "/media/sarkar/ROBOTRACE_2/RoboTracesProject/ROSBAGS_2023_05_13_Originals/2023_05_13/Test3_11_27_C-R"

ros_files = []

# Find all bag files in the given folder
for root, dirs, files in os.walk(folder_path):
    file = {}
    for file_name in files:
        if ".bag" in file_name:
            file['file_name'] = file_name.split('/')[-1]
            file['folder_name'] = root
            file['path'] = os.path.join(root, file_name)
            ros_files.append(file)

df_campaign_files = pd.DataFrame(ros_files)
df_campaign_files.head(5)

file_name  \
0  2023_05_13_11_27_Gera_C-R_Alt.orig.bag   

                                         folder_name  \
0  /media/sarkar/ROBOTRACE_2/RoboTracesProject/RO...   

                                                path  
0  /media/sarkar/ROBOTRACE_2/RoboTracesProject/RO...

In [11]:
bag_file = '/media/sarkar/ROBOTRACE_2/RoboTracesProject/ROSBAGS_2023_05_13_Originals/2023_05_13/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.bag'
topic_to_extract = '/anavs/solution/pos'

with rosbag.Bag(bag_file, 'r') as bag:
    for topic, msg, timestamp in bag.read_messages():
        print(f"Topic: {topic}")
        print(f"Timestamp: {timestamp.to_sec()}")
        print(f"Message data: {msg}\n")

Topic: /rosout
Timestamp: 1683970049.2463088
Message data: header: 
  seq: 25
  stamp: 
    secs: 1683970049
    nsecs: 244083911
  frame_id: ''
level: 2
name: "/record_1683970049207724962"
msg: "Subscribing to /rosout_agg"
file: "/tmp/binarydeb/ros-noetic-rosbag-1.16.0/src/recorder.cpp"
function: "shared_ptr<ros::Subscriber> rosbag::Recorder::subscribe"
line: 256
topics: 
  - /rosout

Topic: /rosout
Timestamp: 1683970049.2463205
Message data: header: 
  seq: 26
  stamp: 
    secs: 1683970049
    nsecs: 244808329
  frame_id: ''
level: 2
name: "/record_1683970049207724962"
msg: "Subscribing to /tf"
file: "/tmp/binarydeb/ros-noetic-rosbag-1.16.0/src/recorder.cpp"
function: "shared_ptr<ros::Subscriber> rosbag::Recorder::subscribe"
line: 256
topics: 
  - /rosout

Topic: /rosout
Timestamp: 1683970049.246322
Message data: header: 
  seq: 27
  stamp: 
    secs: 1683970049
    nsecs: 245491070
  frame_id: ''
level: 2
name: "/record_1683970049207724962"
msg: "Subscribing to /tf_static"
file: "/

In [3]:
# The folder in which you want to save the .csv and .p files and you can also define the folder name 
folder_path = "/media/sarkar/ROBOTRACE_2/Bag/Map"

#folder_path = bagreader('/home/user/Bagfile_map/Gera_Odometry_GPS_Alt_R-C/2023_05_13_11_46_Gera_R-C_Alt.orig.bag')

# Defining relevant topics and data fields
result_params = {
    "rosaria_pose": [ '/RosAria/pose', ['pose.pose.position.x', 'pose.pose.position.y']]
}

for index, measurements in df_campaign_files.iterrows():
    folder_name = measurements.folder_name.split("/")[-1]
    print(f"{index}, {folder_name: <25}")

    if not os.path.exists(os.path.join(folder_path, folder_name)):
            os.makedirs(os.path.join(folder_path, folder_name))
    for result in result_params:
        df = pd.DataFrame()
        if not os.path.isfile(os.path.join(folder_path, folder_name, result+".p")):
            print(f"Processing..    {result}")
            try:
                with AnyReader([Path(measurements['path'])]) as reader:
                    df = get_dataframe(reader,
                                        result_params[result][0],
                                        result_params[result][1])
                df.to_pickle(os.path.join(folder_path, folder_name, result+'.p'))
                df.to_csv(os.path.join(folder_path, folder_name, result+'.csv'))
            except Exception as e:
                print(f"Error.. {result}")
                print(f"{e}")
        else:
            print(f"Data file exist..   {result}")

0, Test3_11_27_C-R          
Processing..    rosaria_pose


In [4]:
f1 = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/rosaria_pose.csv'
df = pd.read_csv(f1)
df.head(5)

Unnamed: 0  pose.pose.position.x  pose.pose.position.y
0  2023-05-13 09:27:29.526644313               207.861              -166.455
1  2023-05-13 09:27:29.623154046               207.861              -166.455
2  2023-05-13 09:27:29.718996429               207.861              -166.455
3  2023-05-13 09:27:29.831233910               207.861              -166.455
4  2023-05-13 09:27:29.926200452               207.861              -166.455

In [5]:
# The .csv file path created from above step
f1 = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/rosaria_pose.csv'

# To read the path
df = pd.read_csv(f1)

# Access to the specific column
column_name_x = 'pose.pose.position.x'
column_name_y = 'pose.pose.position.y'

# Find difference between the values for X column
selected_column_x = df[column_name_x]
diff_x = selected_column_x.diff()

# Find difference between the values for Y column
selected_column_y = df[column_name_y]
diff_y = selected_column_y.diff()

# Find averave value from the difference value
average_diff_x = diff_x.mean()
average_diff_y = diff_y.mean()

# Saving the average value in CSV formate
timestamp_column = df.columns[0]
timestamps = df[timestamp_column]
result_df = pd.DataFrame({'timestamp': timestamps, 'x_diff': average_diff_x, 'y_diff': average_diff_y})
#result_df_x = pd.DataFrame({'average_diff_x': [average_diff_x]})
#result_df_y = pd.DataFrame({'average_diff_y': [average_diff_y]})

result_file_path = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/result.csv'
#result_file_path_x = '/home/user/Bagfile_map/Test_pos/Test3_11_27_C-R/result_file_x.csv'
#result_file_path_y = '/home/user/Bagfile_map/Test_pos/Test3_11_27_C-R/result_file_y.csv'

result_df.to_csv(result_file_path, index=False)
#result_df_x.to_csv(result_file_path_x, index=False)
#result_df_y.to_csv(result_file_path_y, index=False)

# Print all the values
print("Average differences x:", average_diff_x)
print("Average differences y:", average_diff_y)

print("Result saved to:", result_file_path)
#print("Result saved to:", result_file_path_x)
#print("Result saved to:", result_file_path_y)



Average differences x: -0.007509607821103495
Average differences y: -0.035903921788965044
Result saved to: /media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/result.csv


In [7]:
f2 = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/result.csv'
df = pd.read_csv(f2)

df.head(5)

timestamp   x_diff    y_diff
0  2023-05-13 09:27:29.526644313 -0.00751 -0.035904
1  2023-05-13 09:27:29.623154046 -0.00751 -0.035904
2  2023-05-13 09:27:29.718996429 -0.00751 -0.035904
3  2023-05-13 09:27:29.831233910 -0.00751 -0.035904
4  2023-05-13 09:27:29.926200452 -0.00751 -0.035904

In [10]:
f2 = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/result.csv'

csv_df = pd.read_csv(f2)
csv_df['timestamp'] = pd.to_datetime(csv_df[csv_df.columns[0]])
csv_data = csv_df.set_index('timestamp').to_dict()

input_bag_path = '/media/sarkar/ROBOTRACE_2/RoboTracesProject/ROSBAGS_2023_05_13_Originals/2023_05_13/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.bag'
output_bag_path = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.created.bag'

with rosbag.Bag(input_bag_path, 'r') as input_bag:
    with rosbag.Bag(output_bag_path, 'w') as output_bag:
        for topic, msg, timestamp in input_bag.read_messages():
            if topic == '/anavs/solution/pos':
                if timestamp in csv_data:
                        #value_x = value_x_diff_topic[index]
                        #value_y = value_y_diff_topic[index]
                
                    modified_msg = PointStamped()
                    print(timestamp)
                
                    modified_msg.point.x = msg.point.x + df['x_diff'][csv_index]
                    output_bag.write(topic, modified_msg, timestamp)
                
                    modified_msg.point.y = msg.point.y + df['y_diff'][csv_index]
                    output_bag.write(topic, modified_msg, timestamp)
                
                else:
                    output_bag.write(topic, msg, timestamp)
            else:
                output_bag.write(topic, msg, timestamp)
        

In [8]:
output_bag_path = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.created.bag'
f2 = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/result.csv'

csv_df2 = pd.read_csv(f2)
csv_df2['timestamp'] = pd.to_datetime(csv_df2[csv_df2.columns[0]])

matching_timestamps = []

with rosbag.Bag(output_bag_path, 'r') as bag:
    for topic, _, timestamp in bag.read_messages():
        bag_timestamp = timestamp.to_sec()
        matching_csv_rows = csv_df2[csv_df2['timestamp'].apply(lambda x: x.timestamp()) == bag_timestamp]
        
        if not matching_csv_rows.empty:
            matching_timestamps.append((bag_timestamp, matching_csv_rows))
            
    for timestamp, matching_rows in matching_timestamps:
        print(f"Matching Timestamp: {timestamp}")
        for index, row in matching_rows.iterrows():
            print(f"Matching CSV Row: {row}")
        
        #for index, csv_timestamp in csv_df2['timestamp'].iteritems():
        #    if timestamp.to_sec() == csv_timestamp.timestamp():
        #        print(f"Matched CSV Timestamp: {csv_timestamp}")
        #        print(f"CSV Value: {csv_df['value_column'][index]}")

KeyboardInterrupt: 

In [8]:
f2 = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/result.csv'
df = pd.read_csv(f2)

#timestamp_column_final = df.columns[1]
df['timestamp'] = pd.to_datetime(df[df.columns[0]])
#csv_timestamps = pd.to_datetime(df['timestamp'])
#value_x_diff_topic = df['x_diff'].tolist()
#value_y_diff_topic = df['y_diff'].tolist()

input_bag_path = '/media/sarkar/ROBOTRACE_2/RoboTracesProject/ROSBAGS_2023_05_13_Originals/2023_05_13/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.bag'
output_bag_path = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.created.bag'

with rosbag.Bag(input_bag_path, 'r') as input_bag:
    with rosbag.Bag(output_bag_path, 'w') as output_bag:
        csv_index = 0
        for topic, msg, timestamp in input_bag.read_messages():
            
            if topic == '/anavs/solution/pos':
                
                while csv_index < len(df) and df['timestamp'][csv_index].to_datetime() <= timestamp.to_sec():
                    if df['timestamp'][csv_index].to_datetime() == timestamp.to_sec():
        
                        #value_x = value_x_diff_topic[index]
                        #value_y = value_y_diff_topic[index]
                
                        modified_msg = PointStamped()
                
                        modified_msg.point.x = msg.point.x + df['x_diff'][csv_index]
                        output_bag.write(topic, modified_msg, timestamp)
                
                        modified_msg.point.y = msg.point.y + df['y_diff'][csv_index]
                        output_bag.write(topic, modified_msg, timestamp)
                
                    else:
                        output_bag.write(topic, msg, timestamp)
        
            csv_index += 1
        else:
            output_bag.write(topic, msg, timestamp)
        

AttributeError: 'Timestamp' object has no attribute 'to_datetime'

In [43]:
ave_value = '/home/user/Bagfile_map/Test_pos/Test3_11_27_C-R/result_file_x.csv'
df = pd.read_csv(ave_value)
value_to_add = df['average_diff_x'].iloc[0]

input = '/media/user/ROBOTRACE_2/RoboTracesProject/ROSBAGS_2023_05_13_Originals/2023_05_13/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.bag'
output = '/home/user/Bagfile_map/Gera_Odometry_GPS_Alt_R-C/2023_05_13_11_27_Gera_C-R_Alt.orig.bag'

with rosbag.Bag(input, 'r') as input_bag:
    with rosbag.Bag(output, 'w') as output_bag:
        for topic, msg, timestamp in input_bag.read_messages():
            
            if topic == '/anavs/solution/pos':
                modified_msg = PointStamped()
                modified_msg.header = msg.header
                modified_msg.point.x = msg.point.x + value_to_add
                output_bag.write(topic, modified_msg, timestamp)
            else:
                output_bag.write(topic, msg, timestamp)

In [44]:
ave_value = '/home/user/Bagfile_map/Test_pos/Test3_11_27_C-R/result_file_y.csv'
df = pd.read_csv(ave_value)
value_to_add = df['average_diff_y'].iloc[0]

input = '/home/user/Bagfile_map/Gera_Odometry_GPS_Alt_R-C/2023_05_13_11_27_Gera_C-R_Alt.orig.bag'
output = '/home/user/Bagfile_map/Gera_Odometry_GPS_Alt_R-C/2023_05_13_11_27_Gera_C-R_Alt.orig1.bag'

with rosbag.Bag(input, 'r') as input_bag:
    with rosbag.Bag(output, 'w') as output_bag:
        for topic, msg, timestamp in input_bag.read_messages():
            
            if topic == '/anavs/solution/pos':
                modified_msg = PointStamped()
                modified_msg.header = msg.header
                modified_msg.point.x = msg.point.y + value_to_add
                output_bag.write(topic, modified_msg, timestamp)
            else:
                output_bag.write(topic, msg, timestamp)

Changing the GNSS message type from 'geometry_msgs/PointStamped' to 'sensor_msgs/NavSatFix'

In [9]:
input = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.created.bag'
output = '/media/sarkar/ROBOTRACE_2/Bag/Map/Test3_11_27_C-R/2023_05_13_11_27_Gera_C-R_Alt.orig.created.nav.bag'

with rosbag.Bag(input, 'r') as input_bag:
    with rosbag.Bag(output, 'w') as output_bag:
        for topic, msg, timestamp in input_bag.read_messages(): 
            if topic == '/anavs/solution/pos':
                modified_msg = NavSatFix()
                modified_msg.header = msg.header
                modified_msg.latitude = msg.point.x
                modified_msg.longitude = msg.point.y
                modified_msg.altitude = msg.point.z
                output_bag.write(topic, modified_msg, timestamp)
            else:
                output_bag.write(topic, msg, timestamp)        
